In [1]:
# Script to calculate generality and  application data
# Generality: how diverse is the impact of a patent
# This is done by calculating the herfindal index of citing patents

# Feb 7th, 2020
# While the previous version is already up, I want to improve the script
# I want to make calculations with only one script
# Also, I want to compare different class systems
# this version took 10 minutes - i am moving the old version away

# Jan 16th, 2020
# Due to performance problems in the HPC, this script was divided in two, the script following this is generality_2
# generality > 1 is not an error, but a consequence of adopting WIPO
# it seems that the original calculation had only one class per patent
# WIPO provides multiple classes - so when you divide by the total number of citations, 
#  you do not have the proportion of classes cited anymore
# to correct this issue, I can calculate Generality and Originality based only on the first WIPO class

# Jan 13th, 2020
# Script is running but there are two major issues
# - there should not exist generality > 1 , so there is an error in calculation
# - too many NANs (about 400k), but I will tackle this issue in 'too_many_nans.ipynb'

# to tackle the first problem, I'll begin by creating a subset of the database
# to do that, I'll use USPTO classification system

In [2]:
import pandas as pd
import numpy as np
import re

import dask.dataframe as dd
from dask.delayed import delayed

import glob
import graphviz

file_list=glob.glob("data/citation/*")
classification = 'data/wipo.parquet.gz'
dst= 'data/generality.parquet.gz'

dfs = [dd.read_parquet(f, columns=['patent_id']) for f in file_list]
class_df=pd.read_parquet(classification, columns=['wipo_sector_id'])

In [3]:
def join_class(df, class_df):
    df=df.merge(class_df, how='inner', right_index=True, left_index=True)
    return df

In [4]:
#this function reads the custom-made wipo groups and prepare the dict for aggregation
#the aggregation features one count and sums for all classes
def wipo_categories():
    file_classes = 'data/classes.csv.gz'
    classes=pd.read_csv(file_classes, compression='gzip')
    classes=classes[classes['system']=='wipo_field_id'].sector_title.unique().tolist()
    aggregation={}
    for i, element in enumerate(classes):
        if i==0:
                aggregation[element]=['count','sum']
        else:
            aggregation[element]='sum'
    return aggregation

In [5]:
#this function calculate the terms that will be used later to calculate the originality/generality
#it groups by the index and calculate total citation and the sum of citations in each class

def prepare_df(df):
#     aggregation=wipo_categories()
    df=delayed(pd.get_dummies)(df, columns=['wipo_sector_id'])
    df2=df.groupby(df.index).sum()
#     df2.columns = ['_'.join(col).strip() for col in df2.columns.values] #flatten the index (https://www.roelpeters.be/how-to-flatten-a-multiindex-pandas-dataframe/)
    return df2

In [6]:
# receives a table made by prepare_df and calculates 1-herfindal
# this function calculates generality based on Herfindal index
# Herfindal is the sum of the squares divided by the square of the sum of citations
# it is a measure of concentration

# i separate from prepare_df() to make testing easier
def gen_orig(df):
    return 1-(np.square(df).sum(axis='columns')/np.square(df.sum(axis='columns')))


In [7]:
for i,dfx in enumerate(dfs):
    dfx=join_class(dfx, class_df)
    if i==0:
        df=dfx
    else:
        df=dd.concat([df,dfx])

In [8]:
# patent_id is the citing patent
# citation_id (the index) is the cited patent

In [9]:
# generality=delayed(generality)(df)
df=df.repartition(npartitions=50)
df=delayed(prepare_df)(df)
df=delayed(gen_orig)(df)

In [10]:
df.visualize()

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.878001 to fit


In [11]:
%%time
df.compute().to_parquet(dst, compression='gzip')

CPU times: user 9min 33s, sys: 1min 44s, total: 11min 17s
Wall time: 13min 59s


Delayed('to_parquet-ca29a2ad-066c-4411-9cec-6b2ad5eb42eb')

In [12]:
#its a measure of concentration
# as defined in Hall et al, 2001

def generality(df):
    total_citation=np.square(df.groupby(df.index).count().iloc[:,0])
    df=df.groupby(df.index).sum().fillna(0)
    df_squared=np.square(df) #element-wise squaring
    df_squared=df_squared.sum(axis='columns') #sum all columns, per row
    df=dd.concat([df_squared, total_citation], axis=1)
    generality=1-(df['df_squared']/df['total_citation'])    